In [1]:
import folium

import matplotlib as mpl

mpl.rcParams['axes.unicode_minus'] = False

import matplotlib.pyplot as plt

plt.rcParams["font.size"] = 10  # 글꼴 크기 설정
plt.rcParams["font.family"] = "NanumGothicCoding"  # 글꼴 설정

import numpy as np
import pandas as pd
from pandas.io.json import json_normalize

pd.options.display.float_format = '{:,}'.format

import warnings

warnings.filterwarnings("ignore")

import requests

# 서울자전거 따릉이

In [2]:
target_site = 'https://www.bikeseoul.com/app/station/getStationRealtimeStatus.do'
req = requests.post(target_site, data={
    'MIME 유형': 'application/x-www-form-urlencoded; charset=UTF-8',
    'stationGrpSeq': 'ALL',
    'tabld': ''
})
print(req)
print(type(req.text))

# json 모듈의 loads() 메서드로 크롤링한 json 타입의 문자열을 파이썬에서 사용하기 위해 딕셔너리 타입으로 변환한다.
# bikeseoul = json.loads(req.text)

# requests 모듈의 json() 메서드로 크롤링한 json 타입의 문자열을 파이썬에서 사용하기 위해 딕셔너리 타입으로 변환한다.
bikeseoul = req.json()
print(type(bikeseoul))

bikeseoul

<Response [200]>
<class 'str'>
<class 'dict'>


{'stationImgPath': '/nas_link/spb/attachFiles/file_admin/basePath',
 'appUserSessionVO': {'usrSeq': None,
  'encPwd': None,
  'usrClsCd': None,
  'usrDeviceId': None,
  'snsType': None,
  'voucherEndDttm': None,
  'voucherSeq': None,
  'loginId': None,
  'mbId': None,
  'mpnLostYn': None,
  'lang': 'LAG_001',
  'appOsType': None,
  'regDttm': None,
  'authCiVal': None,
  'authClsCd': None,
  'mbTelNo': None,
  'mbEmailName': None,
  'mbPostNo': None,
  'mbAddr1': None,
  'mbAddr2': None,
  'parentSexCd': None,
  'parentBirthDate': None,
  'parentMpnNo': None,
  'emailSendAgreeYn': None,
  'lastLoginDttm': None,
  'mbWgt': None,
  'langClsCd': None,
  'leaveYn': None,
  'leaveReasonCd': None,
  'leaveDttm': None,
  'mbInfoColecAgreeDttm': None,
  'mpnLostDttm': None,
  'pagingYn': None,
  'usrIp': None,
  'partyVoucherSeq': None,
  'elecVoucherSeq': None,
  'requestSeq': None,
  'usrDeviceType': None,
  'snsId': None,
  'usrType': None,
  'viewFlg': 'list',
  'usrBirthDate': None,
  'se

In [3]:
# pandas.io.json 모듈의 json_normalize() 메서드로 json에서 변환된 dict를 pandas DataFrame으로 변환한다.
# json_normalize(dict, 'key')
bikeseoul_df = json_normalize(bikeseoul, 'realtimeList')
print(type(bikeseoul_df))
print(len(bikeseoul_df))
bikeseoul_df.columns

<class 'pandas.core.frame.DataFrame'>
2696


Index(['stationId', 'stationImgFileName', 'stationName', 'stationLongitude',
       'stationLatitude', 'rackTotCnt', 'parkingBikeTotCnt',
       'parkingQRBikeCnt', 'parkingELECBikeCnt', 'stationSeCd', 'mode'],
      dtype='object')

In [4]:
bikeseoul_df

stationId stationImgFileName      stationName stationLongitude  \
0         ST-4                     102. 망원역 1번출구 앞     126.91062927   
1         ST-5                     103. 망원역 2번출구 앞     126.91083527   
2         ST-6                     104. 합정역 1번출구 앞     126.91498566   
3         ST-7                     105. 합정역 5번출구 앞     126.91482544   
4         ST-8                     106. 합정역 7번출구 앞     126.91282654   
...        ...                ...              ...              ...   
2691   ST-3170                       5861. 보라주유소 앞     126.92352295   
2692   ST-3187                      5862. 당산역11번출구     126.90145874   
2693   ST-3200                          5864.장훈고 앞     126.91397858   
2694   ST-3161                       6053. 중부세무서 앞     126.99066162   
2695   ST-1747                                상담센터     127.03565979   

     stationLatitude rackTotCnt parkingBikeTotCnt parkingQRBikeCnt  \
0        37.55564880         15                 0               25   
1        37.55495071         14                 0               27   
2        37.55062866         13                 0               11   
3        37.55000687          5                 0                3   
4        37.54864502         12                 0               12   
...              ...        ...               ...              ...   
2691     37.51319885         10                 0                4   
2692     37.53363037         14                 0               11   
2693     37.51156998          8                 0                8   
2694     37.56092453          5                 0               13   
2695     37.57164001          2                 0                1   

     parkingELECBikeCnt stationSeCd  mode  
0                     9     RAK_002  None  
1                     1     RAK_002  None  
2                     0     RAK_002  None  
3                     0     RAK_002  None  
4                     0     RAK_002  None  
...                 ...         ...   ...  
2691                  2     RAK_002  None  
2692                  1     RAK_002  None  
2693                  0     RAK_002  None  
2694                  1     RAK_002  None  
2695                  0     RAK_001  None  

[2696 rows x 11 columns]

realtimeList
- stationId: 대여소 id
- stationName: 대여소 이름
- stationLongitude: 대여소 경도
- stationLatitude: 대여소 위도
- rackTotCnt: 주차 가능한 자전거 대수
- parkingQRBikeCnt: 주차중인 일반 따릉이 대수
- parkingELECBikeCnt: 주차중인 새싹 따릉이 대수

In [5]:
# 필요한 속성만 추출
bikeseoul_df_map = bikeseoul_df[
    ['stationId', 'stationName', 'stationLongitude', 'stationLatitude', 'rackTotCnt', 'parkingQRBikeCnt',
     'parkingELECBikeCnt']
]
bikeseoul_df_map

stationId      stationName stationLongitude stationLatitude rackTotCnt  \
0         ST-4  102. 망원역 1번출구 앞     126.91062927     37.55564880         15   
1         ST-5  103. 망원역 2번출구 앞     126.91083527     37.55495071         14   
2         ST-6  104. 합정역 1번출구 앞     126.91498566     37.55062866         13   
3         ST-7  105. 합정역 5번출구 앞     126.91482544     37.55000687          5   
4         ST-8  106. 합정역 7번출구 앞     126.91282654     37.54864502         12   
...        ...              ...              ...             ...        ...   
2691   ST-3170    5861. 보라주유소 앞     126.92352295     37.51319885         10   
2692   ST-3187   5862. 당산역11번출구     126.90145874     37.53363037         14   
2693   ST-3200       5864.장훈고 앞     126.91397858     37.51156998          8   
2694   ST-3161    6053. 중부세무서 앞     126.99066162     37.56092453          5   
2695   ST-1747             상담센터     127.03565979     37.57164001          2   

     parkingQRBikeCnt parkingELECBikeCnt  
0                  25                  9  
1                  27                  1  
2                  11                  0  
3                   3                  0  
4                  12                  0  
...               ...                ...  
2691                4                  2  
2692               11                  1  
2693                8                  0  
2694               13                  1  
2695                1                  0  

[2696 rows x 7 columns]

In [6]:
# 자료형 확인: object == str
bikeseoul_df_map.dtypes

stationId             object
stationName           object
stationLongitude      object
stationLatitude       object
rackTotCnt            object
parkingQRBikeCnt      object
parkingELECBikeCnt    object
dtype: object

In [7]:
bikeseoul_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2696 entries, 0 to 2695
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stationId           2696 non-null   object
 1   stationName         2696 non-null   object
 2   stationLongitude    2696 non-null   object
 3   stationLatitude     2696 non-null   object
 4   rackTotCnt          2696 non-null   object
 5   parkingQRBikeCnt    2696 non-null   object
 6   parkingELECBikeCnt  2696 non-null   object
dtypes: object(7)
memory usage: 147.6+ KB


In [8]:
# 형변환
bikeseoul_df_map['stationLongitude'] = bikeseoul_df_map['stationLongitude'].astype(float)
bikeseoul_df_map['stationLatitude'] = bikeseoul_df_map['stationLatitude'].astype(float)
bikeseoul_df_map['rackTotCnt'] = bikeseoul_df_map['rackTotCnt'].astype(int)
bikeseoul_df_map['parkingQRBikeCnt'] = bikeseoul_df_map['parkingQRBikeCnt'].astype(int)
bikeseoul_df_map['parkingELECBikeCnt'] = bikeseoul_df_map['parkingELECBikeCnt'].astype(int)
bikeseoul_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2696 entries, 0 to 2695
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   stationId           2696 non-null   object 
 1   stationName         2696 non-null   object 
 2   stationLongitude    2696 non-null   float64
 3   stationLatitude     2696 non-null   float64
 4   rackTotCnt          2696 non-null   int64  
 5   parkingQRBikeCnt    2696 non-null   int64  
 6   parkingELECBikeCnt  2696 non-null   int64  
dtypes: float64(2), int64(3), object(2)
memory usage: 147.6+ KB


In [9]:
bikeseoul_map = folium.Map(
    location=[bikeseoul_df_map['stationLatitude'].mean(), bikeseoul_df_map['stationLongitude'].mean()], zoom_start=11.5)

for _, data in bikeseoul_df_map.iterrows():
    # print(data)
    popup = folium.Popup('{}<br/>일반따릉이: {}대<br/>새싹따릉이: {}대'.format(data['stationName'], data['parkingQRBikeCnt'],
                                                                   data['parkingELECBikeCnt']), max_width=300)
    folium.Marker(location=[data['stationLatitude'], data['stationLongitude']], popup=popup).add_to(bikeseoul_map)

bikeseoul_map.save('./output/bikeseoul_map.html')
bikeseoul_map

# Geo Coding
pip install geopy
- 지오코딩: 주소로 위도, 경도 좌표 얻기
- 역지오코딩: 위도, 경도 좌표로 주소 얻기

In [10]:
from geopy.geocoders import Nominatim

In [11]:
def geocoding(address):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    geo = geolocoder.geocode(address)
    return {'lat': str(geo.latitude), 'lot': str(geo.longitude)}


loc = geocoding('서울특별시 종로구 관철동')
print(loc)

{'lat': '37.56878', 'lot': '126.98563'}


In [12]:
def geocoding_reverse(location):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    return geolocoder.reverse(location)


addr = geocoding_reverse('37.56878, 126.98563')
print(addr)
print(type(addr))
print(str(addr).split(', '))
addrPrint = str(addr).split(', ')
print(addrPrint[-3], addrPrint[-4], addrPrint[-5])

서울한양도성, 종로10길, 관철동, 종로1·2·3·4가동, 종로구, 서울, 03164, 대한민국
<class 'geopy.location.Location'>
['서울한양도성', '종로10길', '관철동', '종로1·2·3·4가동', '종로구', '서울', '03164', '대한민국']
서울 종로구 종로1·2·3·4가동


In [13]:
bikeseoul_df_map['goo'] = np.NaN
bikeseoul_df_map['dong'] = np.NaN
bikeseoul_df_map

stationId      stationName  stationLongitude  stationLatitude  \
0         ST-4  102. 망원역 1번출구 앞      126.91062927       37.5556488   
1         ST-5  103. 망원역 2번출구 앞      126.91083527      37.55495071   
2         ST-6  104. 합정역 1번출구 앞      126.91498566      37.55062866   
3         ST-7  105. 합정역 5번출구 앞      126.91482544      37.55000687   
4         ST-8  106. 합정역 7번출구 앞      126.91282654      37.54864502   
...        ...              ...               ...              ...   
2691   ST-3170    5861. 보라주유소 앞      126.92352295      37.51319885   
2692   ST-3187   5862. 당산역11번출구      126.90145874      37.53363037   
2693   ST-3200       5864.장훈고 앞      126.91397858      37.51156998   
2694   ST-3161    6053. 중부세무서 앞      126.99066162      37.56092453   
2695   ST-1747             상담센터      127.03565979      37.57164001   

      rackTotCnt  parkingQRBikeCnt  parkingELECBikeCnt  goo  dong  
0             15                25                   9  NaN   NaN  
1             14                27                   1  NaN   NaN  
2             13                11                   0  NaN   NaN  
3              5                 3                   0  NaN   NaN  
4             12                12                   0  NaN   NaN  
...          ...               ...                 ...  ...   ...  
2691          10                 4                   2  NaN   NaN  
2692          14                11                   1  NaN   NaN  
2693           8                 8                   0  NaN   NaN  
2694           5                13                   1  NaN   NaN  
2695           2                 1                   0  NaN   NaN  

[2696 rows x 9 columns]

In [14]:
'''
for i in range(bikeseoul_df_map.shape[0])[:]:
    loc = '{}, {}'.format(bikeseoul_df_map.loc[i, 'stationLatitude'], bikeseoul_df_map.loc[i, 'stationLongitude'])
    # print(loc)
    addr = geocoding_reverse(loc)
    # print(addr)
    addr = str(addr).split(', ')
    # print(addr)
    # print(addr[-4], addr[-5])
    try:
        bikeseoul_df_map.loc[i, 'goo'] = addr[-4]
    except IndexError:
        print(f'{i}번째 [-4] 없음')
    try:
        bikeseoul_df_map.loc[i, 'dong'] = addr[-5]
    except IndexError:
        print(f'{i}번째 [-5] 없음')

bikeseoul_df_map
'''
pass

In [15]:
# bikeseoul_df_map.to_csv('./output/bikeseoul_map_addr.csv', index=False)

In [16]:
pd.read_csv('./output/bikeseoul_map_addr.csv')

stationId      stationName  stationLongitude  stationLatitude  \
0         ST-4  102. 망원역 1번출구 앞      126.91062927       37.5556488   
1         ST-5  103. 망원역 2번출구 앞      126.91083527      37.55495071   
2         ST-6  104. 합정역 1번출구 앞      126.91498566      37.55062866   
3         ST-7  105. 합정역 5번출구 앞      126.91482544      37.55000687   
4         ST-8  106. 합정역 7번출구 앞      126.91282654      37.54864502   
...        ...              ...               ...              ...   
2690   ST-3170    5861. 보라주유소 앞      126.92352295      37.51319885   
2691   ST-3187   5862. 당산역11번출구      126.90145874      37.53363037   
2692   ST-3200       5864.장훈고 앞      126.91397858      37.51156998   
2693   ST-3161    6053. 중부세무서 앞      126.99066162      37.56092453   
2694   ST-1747             상담센터      127.03565979      37.57164001   

      parkingQRBikeCnt  parkingELECBikeCnt  total   goo   dong  
0                   21                   8     29   마포구    서교동  
1                   20                   1     21   마포구   망원1동  
2                    7                   0      7   마포구    서교동  
3                    0                   0      0   마포구    서교동  
4                    8                   0      8   마포구    합정동  
...                ...                 ...    ...   ...    ...  
2690                 4                   2      6  영등포구   신길1동  
2691                 9                   1     10  영등포구   당산2동  
2692                 8                   0      8  영등포구  영등포본동  
2693                13                   1     14    중구     필동  
2694                 0                   0      0   성동구    마장동  

[2695 rows x 9 columns]

In [17]:
error_list = ['ST-212', 'ST-232', 'ST-339', 'ST-152', 'ST-196', 'ST-1771', 'ST-587', 'ST-2402', 'ST-1289', 'ST-1148',
              'ST-1538', 'ST-664', 'ST-668', 'ST-936', 'ST-1224', 'ST-1241', 'ST-1521', 'ST-2352', 'ST-925', 'ST-926',
              'ST-880', 'ST-881', 'ST-781', 'ST-890', 'ST-1168', 'ST-1311', 'ST-2416', 'ST-1861', 'ST-1753', 'ST-1947',
              'ST-1948', 'ST-1949', 'ST-1950', 'ST-1824', 'ST-986', 'ST-2966', 'ST-2828', 'ST-2829', 'ST-2931',
              'ST-2723', 'ST-2535', 'ST-2522', 'ST-3004']
'''
for error in error_list:
    bikeseoul_error = bikeseoul_df_map[bikeseoul_df_map['stationId'] == error]
    # print(bikeseoul_error)
    loc = f'{bikeseoul_error.stationLatitude.iloc[0]}, {bikeseoul_error.stationLongitude.iloc[0]}'
    # print(loc)
    addr = str(geocoding_reverse(loc)).split(', ')
    # print(addr)
    '''
pass

In [18]:
bikeseoul_df_map

stationId      stationName  stationLongitude  stationLatitude  \
0         ST-4  102. 망원역 1번출구 앞      126.91062927       37.5556488   
1         ST-5  103. 망원역 2번출구 앞      126.91083527      37.55495071   
2         ST-6  104. 합정역 1번출구 앞      126.91498566      37.55062866   
3         ST-7  105. 합정역 5번출구 앞      126.91482544      37.55000687   
4         ST-8  106. 합정역 7번출구 앞      126.91282654      37.54864502   
...        ...              ...               ...              ...   
2691   ST-3170    5861. 보라주유소 앞      126.92352295      37.51319885   
2692   ST-3187   5862. 당산역11번출구      126.90145874      37.53363037   
2693   ST-3200       5864.장훈고 앞      126.91397858      37.51156998   
2694   ST-3161    6053. 중부세무서 앞      126.99066162      37.56092453   
2695   ST-1747             상담센터      127.03565979      37.57164001   

      rackTotCnt  parkingQRBikeCnt  parkingELECBikeCnt  goo  dong  
0             15                25                   9  NaN   NaN  
1             14                27                   1  NaN   NaN  
2             13                11                   0  NaN   NaN  
3              5                 3                   0  NaN   NaN  
4             12                12                   0  NaN   NaN  
...          ...               ...                 ...  ...   ...  
2691          10                 4                   2  NaN   NaN  
2692          14                11                   1  NaN   NaN  
2693           8                 8                   0  NaN   NaN  
2694           5                13                   1  NaN   NaN  
2695           2                 1                   0  NaN   NaN  

[2696 rows x 9 columns]

In [19]:
bike_2022 = pd.read_csv('./data/bike_2022.csv')
# bike_2022[['goo', 'dong']].head()

In [20]:
bikeseoul_df_map['goo'] = bike_2022['goo']
bikeseoul_df_map['dong'] = bike_2022['dong']
bikeseoul_df_map.head()

stationId      stationName  stationLongitude  stationLatitude  rackTotCnt  \
0      ST-4  102. 망원역 1번출구 앞      126.91062927       37.5556488          15   
1      ST-5  103. 망원역 2번출구 앞      126.91083527      37.55495071          14   
2      ST-6  104. 합정역 1번출구 앞      126.91498566      37.55062866          13   
3      ST-7  105. 합정역 5번출구 앞      126.91482544      37.55000687           5   
4      ST-8  106. 합정역 7번출구 앞      126.91282654      37.54864502          12   

   parkingQRBikeCnt  parkingELECBikeCnt  goo  dong  
0                25                   9  마포구   서교동  
1                27                   1  마포구  망원1동  
2                11                   0  마포구   서교동  
3                 3                   0  마포구   서교동  
4                12                   0  마포구   합정동

In [25]:
# bikeseoul_df_map_goo = bikeseoul_map[(bikeseoul_df_map['goo'] == '종로구') | (bikeseoul_df_map['goo'] == '용산구')]
bikeseoul_map = folium.Map(
    location=[bikeseoul_df_map['stationLatitude'].mean(), bikeseoul_df_map['stationLongitude'].mean()], zoom_start=12)

for index, data in bikeseoul_df_map.iterrows():
    station = data['stationName'].split('.')
    if len(station) == 1:
        stationName = station[0]
    else:
        stationName = station[1].strip()
    popup = folium.Popup('[{}]<br/>일반따릉이: {}대<br/>새싹따릉이: {}대'.format(stationName, data['parkingQRBikeCnt'],
                                                                   data['parkingELECBikeCnt']), max_width=300)
    folium.Marker(location=[data['stationLatitude'], data['stationLongitude']], popup=popup, icon=folium.Icon(color='green', icon='hand-down')).add_to(bikeseoul_map)

bikeseoul_map.save('./output/bikeseoul.html')
bikeseoul_map